In [72]:
import requests

url = "https://www.congress.gov/"

headers = {
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36"
}

response = requests.get(url, headers=headers)

In [73]:
response

<Response [403]>

In [74]:
from playwright.async_api import async_playwright

In [75]:
playwright = await async_playwright().start()
browser = await playwright.chromium.launch(headless=False)

In [76]:
page = await browser.new_page()

In [77]:
await page.goto("https://www.congress.gov/quick-search/legislation?wordsPhrases=artificial%2Bintelligence&wordVariants=on&congressGroups[0]=0&congresses[0]=118&legislationNumbers=&legislativeAction=&sponsor=on&representative=&senator=&q=%7B%22type%22%3A%5B%22bills%22%2C%22resolutions%22%5D%7D&pageSize=250")

<Response url='https://www.congress.gov/quick-search/legislation?wordsPhrases=artificial%2Bintelligence&wordVariants=on&congressGroups%5B0%5D=0&congresses%5B0%5D=118&legislationNumbers=&legislativeAction=&sponsor=on&representative=&senator=&q=%7B%22type%22%3A%5B%22bills%22%2C%22resolutions%22%5D%7D&pageSize=250' request=<Request url='https://www.congress.gov/quick-search/legislation?wordsPhrases=artificial%2Bintelligence&wordVariants=on&congressGroups%5B0%5D=0&congresses%5B0%5D=118&legislationNumbers=&legislativeAction=&sponsor=on&representative=&senator=&q=%7B%22type%22%3A%5B%22bills%22%2C%22resolutions%22%5D%7D&pageSize=250' method='GET'>>

In [78]:
from bs4 import BeautifulSoup

In [79]:
# my_url = "https://www.congress.gov/quick-search/legislation?wordsPhrases=artificial%2Bintelligence&wordVariants=on&congressGroups%5B0%5D=0&congresses%5B0%5D=118&legislationNumbers=&legislativeAction=&sponsor=on&representative=&senator="
# raw_html = requests.get(my_url).content
# print(raw_html)

In [80]:
html_content = await page.content()
html_content

'<!DOCTYPE html><html class="no-js" lang="en"><head>\n    <title>Quick Search | Congress.gov | Library of Congress</title>\n    <meta http-equiv="Content-Type" content="text/html; charset=UTF-8">\n    <meta name="dc.identifier" content="https://www.congress.gov/quick-search/legislation">\n    <meta name="dc.language" content="eng">\n    <meta name="dc.rights" content="Text is government work">\n    <meta name="dc.subject" content="Legislative Data">\n    <meta name="dc.subject" content="Congress">\n    <meta name="dc.title" content="Quick Search">\n    <meta name="dc.type" content="legislation">\n    <meta name="dc.type" content="webpage">\n    <meta name="viewport" content="width=device-width,initial-scale=1">\n    <meta property="og:image" content="https://www.congress.gov/img/opengraph1200by630.jpg">\n    <meta property="og:title" content="Quick Search">\n    <meta property="og:type" content="website">\n    <meta property="og:url" content="https://www.congress.gov/quick-search/legis

In [81]:
soup_doc = BeautifulSoup(html_content, 'html.parser')

In [82]:
headers = soup_doc.find_all("li", class_="compact")
headers

[<li class="compact">
                     1.
                     <span class="result-heading"><a href="/bill/118th-congress/house-bill/10281?q=%7B%22search%22%3A%22artificial%2Bintelligence%22%7D&amp;s=1&amp;r=1">H.R.10281</a> — 118th Congress (2023-2024)</span>
 <span class="result-title bottom-padding">To promote United States leadership in technical standards by directing the National Institute of Standards and Technology and the Department of State to take certain actions to encourage and enable United States participation in developing standards and specifications for artificial intelligence and other critical and emerging technologies, and for other purposes.</span>
 <span class="result-item">
 <strong>Sponsor:</strong> <a href="/member/jay-obernolte/O000019?q=%7B%22search%22%3A%22artificial%2Bintelligence%22%7D" target="_blank">Obernolte, Jay [Rep.-R-CA-23]</a> (Introduced 12/04/2024) <strong>Cosponsors:</strong> (<a href="/bill/118th-congress/house-bill/10281/cosponsors?q=%7B

Find the bill number, description, sponsor, name of committee that introduced the bill step-by-step. Then put them all in a dictionary of lists

In [83]:
bills = []
for header in headers:
    bill ={}
    bill['title'] = header.find('a').text
    desc_tag = header.find("span", class_="result-title bottom-padding")
    bill['desc'] = desc_tag.text if desc_tag else "No Description Found" #my code was breaking in some places because a few bills don't have desc hence put in this condition
    sponsor_tag = header.find("span", class_="result-item")
    bill['sponsor'] = sponsor_tag.find('a').text
    comm_tag = sponsor_tag.find_next_sibling("span", class_="result-item")
    if comm_tag:
         bill['committee'] = comm_tag.text.replace("s:", "").replace("Committee", "").strip()
    else:
        bill['committee'] = ("No Committee Found")
    bills.append(bill)
bills

[{'title': 'H.R.10281',
  'desc': 'To promote United States leadership in technical standards by directing the National Institute of Standards and Technology and the Department of State to take certain actions to encourage and enable United States participation in developing standards and specifications for artificial intelligence and other critical and emerging technologies, and for other purposes.',
  'sponsor': 'Obernolte, Jay [Rep.-R-CA-23]',
  'committee': 'House - Science, Space, and Technology'},
 {'title': 'H.R.10263',
  'desc': 'To require the Federal financial agencies to carry out a study and report on standardized descriptions for vendor-provided artificial intelligence systems, and for other purposes.',
  'sponsor': 'Waters, Maxine [Rep.-D-CA-43]',
  'committee': 'House - Financial Services'},
 {'title': 'H.R.10262',
  'desc': 'AI Act of 2024',
  'sponsor': 'Waters, Maxine [Rep.-D-CA-43]',
  'committee': 'House - Financial Services'},
 {'title': 'H.Res.1600',
  'desc': 'Ex

The date is in a different practically non existent tag within the sponsor's name. it's just a text file. here i'll try to extract the date separately

Just want to note the moment when I had a breakdown after finding out i'll have to do regex for this

In [84]:
import re
for header in headers:
    header_text = str(header)
    match = re.search(r"Introduced\s(\d{2}/\d{2}/\d{4})", header_text)
    date = match.group(1)
    print("Date:", date)

Date: 12/04/2024
Date: 11/26/2024
Date: 11/26/2024
Date: 11/26/2024
Date: 11/21/2024
Date: 11/21/2024
Date: 11/14/2024
Date: 10/04/2024
Date: 10/01/2024
Date: 09/25/2024
Date: 09/25/2024
Date: 09/24/2024
Date: 09/20/2024
Date: 09/20/2024
Date: 09/19/2024
Date: 09/19/2024
Date: 09/18/2024
Date: 09/17/2024
Date: 09/17/2024
Date: 09/16/2024
Date: 09/16/2024
Date: 09/12/2024
Date: 09/09/2024
Date: 09/09/2024
Date: 09/06/2024
Date: 09/06/2024
Date: 09/06/2024
Date: 08/23/2024
Date: 08/23/2024
Date: 08/06/2024
Date: 08/01/2024
Date: 08/01/2024
Date: 07/31/2024
Date: 07/30/2024
Date: 07/30/2024
Date: 07/30/2024
Date: 07/30/2024
Date: 07/30/2024
Date: 07/30/2024
Date: 07/30/2024
Date: 07/24/2024
Date: 07/24/2024
Date: 07/15/2024
Date: 07/15/2024
Date: 07/15/2024
Date: 07/11/2024
Date: 07/10/2024
Date: 07/08/2024
Date: 06/27/2024
Date: 06/25/2024
Date: 06/20/2024
Date: 06/20/2024
Date: 06/14/2024
Date: 06/11/2024
Date: 06/11/2024
Date: 06/11/2024
Date: 06/07/2024
Date: 06/07/2024
Date: 05/23/20

Now add this date to the previous code as "date introduced"

In [85]:
bills = []
for header in headers:
    bill ={}
    bill['title'] = header.find('a').text
    desc_tag = header.find("span", class_="result-title bottom-padding")
    bill['desc'] = desc_tag.text if desc_tag else "No Description Found" 
    header_text = str(header)
    match = re.search(r"Introduced\s(\d{2}/\d{2}/\d{4})", header_text)
    date = match.group(1)
    bill['date introduced'] = date
    sponsor_tag = header.find("span", class_="result-item")
    bill['sponsor'] = sponsor_tag.find('a').text
    comm_tag = sponsor_tag.find_next_sibling("span", class_="result-item")
    if comm_tag:
         bill['committee'] = comm_tag.text.replace("s:", "").replace("Committee", "").strip()
    else:
        bill['committee'] = ("No Committee Found")
    bills.append(bill)
    
bills

[{'title': 'H.R.10281',
  'desc': 'To promote United States leadership in technical standards by directing the National Institute of Standards and Technology and the Department of State to take certain actions to encourage and enable United States participation in developing standards and specifications for artificial intelligence and other critical and emerging technologies, and for other purposes.',
  'date introduced': '12/04/2024',
  'sponsor': 'Obernolte, Jay [Rep.-R-CA-23]',
  'committee': 'House - Science, Space, and Technology'},
 {'title': 'H.R.10263',
  'desc': 'To require the Federal financial agencies to carry out a study and report on standardized descriptions for vendor-provided artificial intelligence systems, and for other purposes.',
  'date introduced': '11/26/2024',
  'sponsor': 'Waters, Maxine [Rep.-D-CA-43]',
  'committee': 'House - Financial Services'},
 {'title': 'H.R.10262',
  'desc': 'AI Act of 2024',
  'date introduced': '11/26/2024',
  'sponsor': 'Waters, Max

In [86]:
len(bills)

150

In [87]:
await page.goto("https://www.congress.gov/advanced-search/legislation?congressGroup[0]=0&congresses[0]=118&congresses[1]=117&congresses[2]=116&congresses[3]=115&congresses[4]=114&congresses[5]=113&congresses[6]=112&congresses[7]=111&congresses[8]=110&congresses[9]=109&congresses[10]=108&congresses[11]=107&congresses[12]=106&congresses[13]=105&congresses[14]=104&congresses[15]=103&congresses[16]=102&congresses[17]=101&congresses[18]=100&congresses[19]=99&congresses[20]=98&congresses[21]=97&congresses[22]=96&congresses[23]=95&congresses[24]=94&congresses[25]=93&legislationNumbers=&restrictionType=includeBillText&restrictionFields[0]=allBillTitles&restrictionFields[1]=summary&summaryField=billSummary&enterTerms=artificial%2Bintelligence%2BAI&wordVariants=true&caseSensitive=true&legislationTypes[0]=hr&legislationTypes[1]=hres&legislationTypes[2]=hjres&legislationTypes[3]=hconres&legislationTypes[4]=hamdt&legislationTypes[5]=s&legislationTypes[6]=sres&legislationTypes[7]=sjres&legislationTypes[8]=sconres&legislationTypes[9]=samdt&legislationTypes[10]=suamdt&public=true&private=true&actionTerms=&legislativeActionWordVariants=true&actionDateBoxCount=2&actionText=&dateOfActionOperator=equal&dateOfActionStartDate=&dateOfActionEndDate=&dateOfActionIsOptions=yesterday&actionText2=&dateOfActionOperator2=equal&dateOfActionStartDate2=&dateOfActionEndDate2=&dateOfActionIsOptions2=yesterday&dateOfActionToggle=multi&legislativeAction=Any&sponsorState=One&member=&sponsorTypes[0]=sponsor&sponsorTypes[1]=sponsor&sponsorTypeBool=OR&dateOfSponsorshipOperator=equal&dateOfSponsorshipStartDate=&dateOfSponsorshipEndDate=&dateOfSponsorshipIsOptions=yesterday&committeeActivity[0]=0&committeeActivity[1]=3&committeeActivity[2]=11&committeeActivity[3]=12&committeeActivity[4]=4&committeeActivity[5]=2&committeeActivity[6]=5&committeeActivity[7]=9&satellite=%5B%5D&search=&submitted=Submitted&id=111122&q=%7B%22type%22%3A%22bills%22%7D&pageSize=250")

<Response url='https://www.congress.gov/advanced-search/legislation?congressGroup%5B0%5D=0&congresses%5B0%5D=118&congresses%5B1%5D=117&congresses%5B2%5D=116&congresses%5B3%5D=115&congresses%5B4%5D=114&congresses%5B5%5D=113&congresses%5B6%5D=112&congresses%5B7%5D=111&congresses%5B8%5D=110&congresses%5B9%5D=109&congresses%5B10%5D=108&congresses%5B11%5D=107&congresses%5B12%5D=106&congresses%5B13%5D=105&congresses%5B14%5D=104&congresses%5B15%5D=103&congresses%5B16%5D=102&congresses%5B17%5D=101&congresses%5B18%5D=100&congresses%5B19%5D=99&congresses%5B20%5D=98&congresses%5B21%5D=97&congresses%5B22%5D=96&congresses%5B23%5D=95&congresses%5B24%5D=94&congresses%5B25%5D=93&legislationNumbers=&restrictionType=includeBillText&restrictionFields%5B0%5D=allBillTitles&restrictionFields%5B1%5D=summary&summaryField=billSummary&enterTerms=artificial%2Bintelligence%2BAI&wordVariants=true&caseSensitive=true&legislationTypes%5B0%5D=hr&legislationTypes%5B1%5D=hres&legislationTypes%5B2%5D=hjres&legislationTyp

In [88]:
html_content1 = await page.content()
html_content1

'<!DOCTYPE html><html class="no-js" lang="en"><head>\n<style>\n        .new-action-gray-box {\n            background: #e6ebee;\n            padding: 10px;\n            width: calc(100% - 50px);\n        }\n        .new-action-white-box {\n            background: white;\n            padding: 10px;\n            display: inline-block;\n        }\n        .new-action-button-container {\n            display: inline-block;\n            float: right;\n        }\n    </style>    <title>Advanced Search - Legislation | Congress.gov | Library of Congress</title>\n    <meta http-equiv="Content-Type" content="text/html; charset=UTF-8">\n    <meta name="dc.identifier" content="https://www.congress.gov/advanced-search/legislation">\n    <meta name="dc.language" content="eng">\n    <meta name="dc.rights" content="Text is government work">\n    <meta name="dc.subject" content="Legislative Data">\n    <meta name="dc.subject" content="Congress">\n    <meta name="dc.title" content="Advanced Search - Legi

In [89]:
soup_doc1 = BeautifulSoup(html_content1, 'html.parser')

In [90]:
headers1 = soup_doc1.find_all("li", class_="compact")
headers1

[<li class="compact" style="display:none">
                     1.
                     <span class="result-heading"><a href="/bill/118th-congress/house-bill/8756?q=%7B%22search%22%3A%22artificial%2Bintelligence%2BAI%22%7D&amp;s=1&amp;r=1">H.R.8756</a> — 118th Congress (2023-2024)</span>
 <span class="result-title bottom-padding">AI LEAD Act</span>
 <span class="result-item">
 <strong>Sponsor:</strong> <a href="/member/gerald-connolly/C001078?q=%7B%22search%22%3A%22artificial%2Bintelligence%2BAI%22%7D" target="_blank">Connolly, Gerald E. [Rep.-D-VA-11]</a> (Introduced 06/14/2024) <strong>Cosponsors:</strong> (<a href="/bill/118th-congress/house-bill/8756/cosponsors?q=%7B%22search%22%3A%22artificial%2Bintelligence%2BAI%22%7D&amp;s=1&amp;r=1&amp;overview=closed#tabs">2</a>)
         </span>
 <span class="result-item">
 <strong>Committees:</strong> House - Oversight and Accountability; Science, Space, and Technology
         </span>
 <span class="result-item">
 <strong>Latest Action:</str

In [91]:
next_bills = []
for header in headers1:
    new_bill ={}
    new_bill['title'] = header.find('a').text
    desc_tag = header.find("span", class_="result-title bottom-padding")
    new_bill['desc'] = desc_tag.text if desc_tag else "No Description Found" 
    header_text = str(header)
    match = re.search(r"Introduced\s(\d{2}/\d{2}/\d{4})", header_text)
    date = match.group(1)
    new_bill['date introduced'] = date
    sponsor_tag = header.find("span", class_="result-item")
    new_bill['sponsor'] = sponsor_tag.find('a').text
    comm_tag = sponsor_tag.find_next_sibling("span", class_="result-item")
    if comm_tag:
         new_bill['committee'] = comm_tag.text.replace("s:", "").replace("Committee", "").strip()
    else:
        new_bill['committee'] = ("No Committee Found")
    next_bills.append(new_bill)
next_bills

[{'title': 'H.R.8756',
  'desc': 'AI LEAD Act',
  'date introduced': '06/14/2024',
  'sponsor': 'Connolly, Gerald E. [Rep.-D-VA-11]',
  'committee': 'House - Oversight and Accountability; Science, Space, and Technology'},
 {'title': 'S.2293',
  'desc': 'AI LEAD Act',
  'date introduced': '07/13/2023',
  'sponsor': 'Peters, Gary C. [Sen.-D-MI]',
  'committee': 'Senate - Homeland Security and Governmental Affairs'},
 {'title': 'H.R.3831',
  'desc': 'AI Disclosure Act of 2023',
  'date introduced': '06/05/2023',
  'sponsor': 'Torres, Ritchie [Rep.-D-NY-15]',
  'committee': 'House - Energy and Commerce'},
 {'title': 'H.R.4223',
  'desc': 'National AI Commission Act',
  'date introduced': '06/20/2023',
  'sponsor': 'Lieu, Ted [Rep.-D-CA-36]',
  'committee': 'House - Science, Space, and Technology'},
 {'title': 'H.R.9211',
  'desc': 'LIFT AI Act',
  'date introduced': '07/30/2024',
  'sponsor': 'Kean, Thomas H. [Rep.-R-NJ-7]',
  'committee': 'House - Science, Space, and Technology'},
 {'titl

In [92]:
len(next_bills)

164

In [93]:
big_list = bills + next_bills
len(big_list)

314

In [94]:
import pandas as pd
df = pd.DataFrame(big_list)
df

title                                               desc  \
0     H.R.10281  To promote United States leadership in technic...   
1     H.R.10263  To require the Federal financial agencies to c...   
2     H.R.10262                                     AI Act of 2024   
3    H.Res.1600  Expressing the sense of the House of Represent...   
4     H.R.10212                                  SCAM Platform Act   
..          ...                                                ...   
309      S.2943  National Defense Authorization Act for Fiscal ...   
310    H.R.4909  National Defense Authorization Act for Fiscal ...   
311    H.R.4577              Consolidated Appropriations Act, 2001   
312    H.R.3131  National High-Performance Computer Technology ...   
313      S.1067             High-Performance Computing Act of 1990   

    date introduced                             sponsor  \
0        12/04/2024       Obernolte, Jay [Rep.-R-CA-23]   
1        11/26/2024       Waters, Maxine [Rep.-D-CA-43]   
2        11/26/2024       Waters, Maxine [Rep.-D-CA-43]   
3        11/26/2024  McHenry, Patrick T. [Rep.-R-NC-10]   
4        11/21/2024       Curtis, John R. [Rep.-R-UT-3]   
..              ...                                 ...   
309      05/18/2016            McCain, John [Sen.-R-AZ]   
310      04/12/2016      Thornberry, Mac [Rep.-R-TX-13]   
311      06/01/2000  Porter, John Edward [Rep.-R-IL-10]   
312      08/03/1989        Walgren, Doug [Rep.-D-PA-18]   
313      05/18/1989       Gore, Albert, Jr. [Sen.-D-TN]   

                                             committee  
0               House - Science, Space, and Technology  
1                           House - Financial Services  
2                           House - Financial Services  
3                           House - Financial Services  
4                          House - Energy and Commerce  
..                                                 ...  
309                            Senate - Armed Services  
310                             House - Armed Services  
311                             House - Appropriations  
312              House - Science, Space and Technology  
313  Senate - Commerce, Science, and Transportation...  

[314 rows x 5 columns]

In [95]:
df = df.drop_duplicates()
df

title                                               desc  \
0     H.R.10281  To promote United States leadership in technic...   
1     H.R.10263  To require the Federal financial agencies to c...   
2     H.R.10262                                     AI Act of 2024   
3    H.Res.1600  Expressing the sense of the House of Represent...   
4     H.R.10212                                  SCAM Platform Act   
..          ...                                                ...   
309      S.2943  National Defense Authorization Act for Fiscal ...   
310    H.R.4909  National Defense Authorization Act for Fiscal ...   
311    H.R.4577              Consolidated Appropriations Act, 2001   
312    H.R.3131  National High-Performance Computer Technology ...   
313      S.1067             High-Performance Computing Act of 1990   

    date introduced                             sponsor  \
0        12/04/2024       Obernolte, Jay [Rep.-R-CA-23]   
1        11/26/2024       Waters, Maxine [Rep.-D-CA-43]   
2        11/26/2024       Waters, Maxine [Rep.-D-CA-43]   
3        11/26/2024  McHenry, Patrick T. [Rep.-R-NC-10]   
4        11/21/2024       Curtis, John R. [Rep.-R-UT-3]   
..              ...                                 ...   
309      05/18/2016            McCain, John [Sen.-R-AZ]   
310      04/12/2016      Thornberry, Mac [Rep.-R-TX-13]   
311      06/01/2000  Porter, John Edward [Rep.-R-IL-10]   
312      08/03/1989        Walgren, Doug [Rep.-D-PA-18]   
313      05/18/1989       Gore, Albert, Jr. [Sen.-D-TN]   

                                             committee  
0               House - Science, Space, and Technology  
1                           House - Financial Services  
2                           House - Financial Services  
3                           House - Financial Services  
4                          House - Energy and Commerce  
..                                                 ...  
309                            Senate - Armed Services  
310                             House - Armed Services  
311                             House - Appropriations  
312              House - Science, Space and Technology  
313  Senate - Commerce, Science, and Transportation...  

[236 rows x 5 columns]

In [96]:
repeated_items = df['desc'][df['desc'].duplicated()]
print(len(repeated_items))

41


In [97]:
len(df['desc'].unique())

195

In [112]:
df = df.drop_duplicates(subset=['desc'])
df

title                                               desc  \
0     H.R.10281  To promote United States leadership in technic...   
1     H.R.10263  To require the Federal financial agencies to c...   
2     H.R.10262                                     AI Act of 2024   
3    H.Res.1600  Expressing the sense of the House of Represent...   
4     H.R.10212                                  SCAM Platform Act   
..          ...                                                ...   
308      S.3502                       AI in Government Act of 2018   
309      S.2943  National Defense Authorization Act for Fiscal ...   
311    H.R.4577              Consolidated Appropriations Act, 2001   
312    H.R.3131  National High-Performance Computer Technology ...   
313      S.1067             High-Performance Computing Act of 1990   

    date introduced                             sponsor  \
0        12/04/2024       Obernolte, Jay [Rep.-R-CA-23]   
1        11/26/2024       Waters, Maxine [Rep.-D-CA-43]   
2        11/26/2024       Waters, Maxine [Rep.-D-CA-43]   
3        11/26/2024  McHenry, Patrick T. [Rep.-R-NC-10]   
4        11/21/2024       Curtis, John R. [Rep.-R-UT-3]   
..              ...                                 ...   
308      09/26/2018           Schatz, Brian [Sen.-D-HI]   
309      05/18/2016            McCain, John [Sen.-R-AZ]   
311      06/01/2000  Porter, John Edward [Rep.-R-IL-10]   
312      08/03/1989        Walgren, Doug [Rep.-D-PA-18]   
313      05/18/1989       Gore, Albert, Jr. [Sen.-D-TN]   

                                             committee  
0               House - Science, Space, and Technology  
1                           House - Financial Services  
2                           House - Financial Services  
3                           House - Financial Services  
4                          House - Energy and Commerce  
..                                                 ...  
308  Senate - Homeland Security and Governmental Af...  
309                            Senate - Armed Services  
311                             House - Appropriations  
312              House - Science, Space and Technology  
313  Senate - Commerce, Science, and Transportation...  

[195 rows x 5 columns]

In [110]:
issue_list = df["desc"].tolist()

print(issue_list)

['To promote United States leadership in technical standards by directing the National Institute of Standards and Technology and the Department of State to take certain actions to encourage and enable United States participation in developing standards and specifications for artificial intelligence and other critical and emerging technologies, and for other purposes.', 'To require the Federal financial agencies to carry out a study and report on standardized descriptions for vendor-provided artificial intelligence systems, and for other purposes.', 'AI Act of 2024', 'Expressing the sense of the House of Representatives with respect to the use of artificial intelligence in the financial services and housing industries.', 'SCAM Platform Act', 'TRAIN Act', 'AI Fraud Deterrence Act', 'Ending FCC Meddling in Our Elections Act', 'Next Generation Military Education Act', 'AWARE Act of 2024', 'MedShield Act of 2024', 'Artificial Intelligence Civil Rights Act of 2024', 'Secure A.I. Act of 2024'

In [99]:
df = pd.DataFrame(df)
df

title                                               desc  \
0     H.R.10281  To promote United States leadership in technic...   
1     H.R.10263  To require the Federal financial agencies to c...   
2     H.R.10262                                     AI Act of 2024   
3    H.Res.1600  Expressing the sense of the House of Represent...   
4     H.R.10212                                  SCAM Platform Act   
..          ...                                                ...   
309      S.2943  National Defense Authorization Act for Fiscal ...   
310    H.R.4909  National Defense Authorization Act for Fiscal ...   
311    H.R.4577              Consolidated Appropriations Act, 2001   
312    H.R.3131  National High-Performance Computer Technology ...   
313      S.1067             High-Performance Computing Act of 1990   

    date introduced                             sponsor  \
0        12/04/2024       Obernolte, Jay [Rep.-R-CA-23]   
1        11/26/2024       Waters, Maxine [Rep.-D-CA-43]   
2        11/26/2024       Waters, Maxine [Rep.-D-CA-43]   
3        11/26/2024  McHenry, Patrick T. [Rep.-R-NC-10]   
4        11/21/2024       Curtis, John R. [Rep.-R-UT-3]   
..              ...                                 ...   
309      05/18/2016            McCain, John [Sen.-R-AZ]   
310      04/12/2016      Thornberry, Mac [Rep.-R-TX-13]   
311      06/01/2000  Porter, John Edward [Rep.-R-IL-10]   
312      08/03/1989        Walgren, Doug [Rep.-D-PA-18]   
313      05/18/1989       Gore, Albert, Jr. [Sen.-D-TN]   

                                             committee  
0               House - Science, Space, and Technology  
1                           House - Financial Services  
2                           House - Financial Services  
3                           House - Financial Services  
4                          House - Energy and Commerce  
..                                                 ...  
309                            Senate - Armed Services  
310                             House - Armed Services  
311                             House - Appropriations  
312              House - Science, Space and Technology  
313  Senate - Commerce, Science, and Transportation...  

[236 rows x 5 columns]

In [116]:
issue_list = df["desc"].tolist()

print(issue_list) #i will paste this list in my for loop in the lobbying API notebook

['To promote United States leadership in technical standards by directing the National Institute of Standards and Technology and the Department of State to take certain actions to encourage and enable United States participation in developing standards and specifications for artificial intelligence and other critical and emerging technologies, and for other purposes.', 'To require the Federal financial agencies to carry out a study and report on standardized descriptions for vendor-provided artificial intelligence systems, and for other purposes.', 'AI Act of 2024', 'Expressing the sense of the House of Representatives with respect to the use of artificial intelligence in the financial services and housing industries.', 'SCAM Platform Act', 'TRAIN Act', 'AI Fraud Deterrence Act', 'Ending FCC Meddling in Our Elections Act', 'Next Generation Military Education Act', 'AWARE Act of 2024', 'MedShield Act of 2024', 'Artificial Intelligence Civil Rights Act of 2024', 'Secure A.I. Act of 2024'

In [101]:
df.to_csv('new_congress-bills.csv', index=False)